### Mapping places in Kansai using Folium   

A few quick examples about visualizing information from OpenStreetMap data for the Kansai region in Japan using folium, a python library that allows users to plot interactive maps using Leaflet.js.

I was introduced to folium while checking out this library called [geopatra](https://github.com/Sangarshanan/geopatra), which is a high level interface for folium and kepler plots. Sangarshanan's source code helped me figure out how to work with it pretty quickly, so thank you my dude.

Reference docs for folium : [https://python-visualization.github.io/folium/modules.html](https://python-visualization.github.io/folium/modules.html)

Since folium is an interface on top of leaflet.js, you'll want to look at leaflet documentation to customize your maps further.  
Reference docs for Leaflet: [https://leafletjs.com/reference-1.6.0.html](https://leafletjs.com/reference-1.6.0.html)

Installing geopandas and folium through conda was pretty painless. I'm reading geographic information from a PostGreSQL database.

Why Kansai? It's got pretty castles.

<img src="https://thumbs.dreamstime.com/b/osaka-castle-kansai-japan-42412095.jpg" width=420, height=420>
<div style="text-align:center;">Source: <a href="https://thumbs.dreamstime.com/b/osaka-castle-kansai-japan-42412095.jpg">https://thumbs.dreamstime.com/b/osaka-castle-kansai-japan-42412095.jpg</a></div>

In [1]:
import numpy as np
import geopandas as gpd
import matplotlib.pyplot as plt
import folium
import psycopg2 as pg2
import random
%matplotlib inline

For this notebook, the geographical information was downloaded as a pbf file from [GeoFabrik](http://download.geofabrik.de/) and then loaded on to a PostGreSQL database using the **osm2pgsql** tool. This splits geographical information into different tables like *planet_osm_points*, which contains point information like cafes, hospitals etc and *planet_osm_lines*, which contains information about roads, railway lines etc.
These tables contain geometric information as well as tags which determine what kind of building or road it is, among other things.

I can't read japanese, and most of the the location names are in japanese, oops.

Anway, you can query these tables using psycopg2 and store it into geopandas dataframes. These dataframes, which are vector layers, can be fed straight into the *folium.GeoJson()* method, although we aren't using that in this notebook.

Also you could find castles using the historic key I think.

In [2]:
user = ''
password = ''
port = ''

def get_gdf_from_postgis(query):
    con = pg2.connect(host = 'localhost', database = 'kansai_osm', user = user, password = password, port = port)
    cur = con.cursor()

    df = gpd.read_postgis(query, con, geom_col = 'way', crs = 3857)
    df = df.to_crs(epsg=4326)

    con.close()
    cur.close()
    
    return df

#### Mapping Point Geometry

Finding a nice to place to sit down and drink a refreshing beverage is essential when travelling, so let's plot a thousand odd cafes in the Kansai Region. These can be found using the [amenity](https://wiki.openstreetmap.org/wiki/Key:amenity) key. There are around 6340 cafes present in the OSM data, however plotting all of them may result in a noticeable slowdown.

In [3]:
query = """SELECT osm_id, name, amenity, way 
        FROM planet_osm_point 
        WHERE amenity = 'cafe' 
        LIMIT 1500;"""
cafe_df = get_gdf_from_postgis(query)
cafe_df.head()

osm_id               name amenity  \
0  6065212889                菜の花    cafe   
1  2850298433                ポポロ    cafe   
2  4607332513      コメダ珈琲店 西大路八条店    cafe   
3  5056177122  Living Room パグカフェ    cafe   
4  1735343659              マンガ喫茶    cafe   

                                     way  
0   POINT (135.552885 35.03347239965395)  
1  POINT (135.7202321 34.98343509965054)  
2  POINT (135.7347973 34.98396069965058)  
3  POINT (135.7072065 34.98719359965082)  
4  POINT (135.7047042 34.98922069965093)

The points are being plotted as circles here, given latitude and longitude. You could plot them as markers as well. Markers don't scale well for a large number of points however, might want to look into clustermaps.

You can provide links to the basemap tiles you would like to use. This changes how the world map looks like. A full list of tiles available can be found [here](https://wiki.openstreetmap.org/wiki/Tiles).

In [4]:
map_center = list(reversed(list(cafe_df.iloc[0]['way'].centroid.coords[0])))
folium_map = folium.Map(height = 550, width = 950, location = map_center, tiles = "OpenStreetMap", 
                        attr = "OSM", zoom_start = 8)

for i, row in cafe_df.iterrows():
    cafe_name = row['name']
    if row['name'] is None:
        cafe_name = "(unknown)"
    tooltip_text = cafe_name
    
    lat, lon = row["way"].y, row["way"].x
    folium.Circle(radius = 10, location = [lat, lon], 
                  tooltip = tooltip_text, popup = tooltip_text, fill = True, 
                  color = '#5555FF', fill_color = '#DDDDDD').add_to(folium_map)
    
folium_map

Although you can see the names in japanese in the dataframe, for whatever reason folium, or rather **branca**, a library which renders the html and handles the js, has issues with showing the unicode on the map. So when you hover over the points above, you're going to see some weird characters. For the OpenStreetMap tile layer, the names are on the map anyway.

Now for a little customization. 

If you had some numerical data associated with these cafes, you could color them, change circle radius etc according to the data, such as sales or popularity. Since I don't have that kind of info available, I'm going to color the cafes according to their distance from Kyoto. The closer they are to Kyoto, the more red they appear.

In [5]:
from shapely.geometry import Point
kyoto_coords = Point(135.7681, 35.0116)  #4326 longitude, latitude of kyoto

cafe_df['dist_from_kyoto'] = cafe_df["way"].to_crs(epsg=4326).distance(kyoto_coords)

max_dist, min_dist = cafe_df["dist_from_kyoto"].max(), cafe_df["dist_from_kyoto"].min()
cafe_df["dist_from_kyoto"] = cafe_df["dist_from_kyoto"].apply(lambda x : 
                                                                  255*(1 - (x - min_dist)/(max_dist - min_dist)))

cafe_df["colors"] = cafe_df["dist_from_kyoto"].apply(lambda x : ("#%02x" % int(x)) + "0000")
cafe_df.head()

c:\users\krishnan meep\appdata\local\programs\python\python36\lib\site-packages\ipykernel_launcher.py:4: UserWarning: Geometry is in a geographic CRS. Results from 'distance' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  after removing the cwd from sys.path.


osm_id               name amenity  \
0  6065212889                菜の花    cafe   
1  2850298433                ポポロ    cafe   
2  4607332513      コメダ珈琲店 西大路八条店    cafe   
3  5056177122  Living Room パグカフェ    cafe   
4  1735343659              マンガ喫茶    cafe   

                                     way  dist_from_kyoto   colors  
0   POINT (135.552885 35.03347239965395)       220.016830  #dc0000  
1  POINT (135.7202321 34.98343509965054)       246.075315  #f60000  
2  POINT (135.7347973 34.98396069965058)       248.062463  #f80000  
3  POINT (135.7072065 34.98719359965082)       244.444336  #f40000  
4  POINT (135.7047042 34.98922069965093)       244.180584  #f40000

In [6]:
map_center = list(reversed(list(cafe_df.iloc[0]['way'].centroid.coords[0])))
folium_map = folium.Map(height = 550, width = 950, location = map_center, tiles = "OpenStreetMap", 
                        attr = "OSM", zoom_start = 8)
                        
folium.Circle(radius = 10000, location = (35.0116, 135.7681), 
                  tooltip = "Kyoto", popup = "Kyoto", fill = True, fill_color = "#112200", opacity = 0.8, 
                  color = '#5544CC').add_to(folium_map)

for i, row in cafe_df.iterrows():
    tooltip_text = str(row["dist_from_kyoto"])
    
    lat, lon = row["way"].y, row["way"].x
    folium.Circle(radius = 10, location = [lat, lon], 
                  tooltip = tooltip_text, popup = tooltip_text, fill = True, 
                  color = row["colors"], fill_color = row["colors"]).add_to(folium_map)
    
folium_map